# PILCO: A Model-based Policy Search

Reinforcement learning for real world applications suffer from data inefficiency. Deisenroth & Rasmussen (2011) proposes a model-based policy search method, which is known as PILCO. PILCO uses a Gaussian process (GP) for learning the dynamics of the environment and optimizes a parametric policy function according to the learned dynamics model.

In this notebook, we demonstrate a straight-forward implementation of PILCO. This implementation follows the idea of PILCO and have a few enhancement compared to the published implementation. The enhancement are listed as follows:  

- **Use Monte Carlo integration instead of moment estimation.** We approximate the expected reward using Monte Carlo integration instead of the proposed moment estimation approach. This removes the bias in the expected reward computation and enables a wide range of choices of kernels and policy functions. In the original work, only RBF and linear kernel and only linear and RBF network policy can be used.
- **Use automatic differentiation.** Thanks to automatic differentiation, no gradient derivation is needed.
- **An unified interface of Gaussian process.** MXFusion provides an unified inferface of GP modules. We allows us to easily switch among plan GP, variational sparse GP and stocastic variational GP implementations.

## Preparation

This notebook depends on MXNet, MXFusion and Open AI Gym. These packages can be installed into your Python environment by running the following commands.
```bash
pip install mxnet mxfusion gym
```

Set the global configuration.

In [57]:
import os
os.environ['MXNET_ENGINE_TYPE'] = 'NaiveEngine'
from mxfusion.common import config
config.DEFAULT_DTYPE = 'float64'
%matplotlib inline

## Example: Pendulum


We use the inverted pendulum swingup problem as an example. We use the [Pendulum-v0](https://gym.openai.com/envs/Pendulum-v0/) enironment in Open AI Gym. The task is to swing the pendulum up and balance it at the inverted position. This is a classical control problem and is known to be unsolvable with a linear controller.

To solve this problem with PILCO, it needs three components:

- Execute a policy in an real environment (an Open AI Gym simulator in this example) and collect data.
- Fit a GP model as the model for the dynamics of the environment.
- Optimize the policy given the dynamics model learned from all the data that have been collected so far.

The overall PILCO algorithm is to iterate the above three steps until a policy that can solve the problem is found.

## Execute the Environment 

The Pendulum-v0 environment can be loaded easily.

In [58]:
import gym
env = gym.make('Pendulum-v0')

The state of the pendulum environment is a 3D vector. The first two dimensions are the 2D location of the end point of the pendulum. The third dimension encodes the angular speed of the pendulum. The action space is a 1D vector in [-2, 2].

We write a helper function for executing the environment with a given policy.

In [37]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib import animation

def run_one_episode(env, policy, initial_state=None, max_steps=200, verbose=False, render=False):
    """
    Drives an episode of the OpenAI gym environment using the policy to decide next actions.
    """
    observation = env.reset()
    if initial_state is not None:
        env.env.state = initial_state
        observation = env.env._get_obs()
    env._max_episode_steps = max_steps
    step_idx = 0
    done = False
    total_reward = 0
    frames = []
    all_actions = []
    all_observations = [observation]
    while not done:
        if render:
            frames.append(env.render(mode = 'rgb_array'))
        if verbose:
            print(observation)
        action = policy(observation)
        observation, reward, done, info = env.step(action)
        all_observations.append(observation)
        all_actions.append(action)
        total_reward += reward
        step_idx += 1
        if done or step_idx>=max_steps-1:
            print("Episode finished after {} timesteps because {}".format(step_idx+1, "'done' reached" if done else "Max timesteps reached"))
            break
    if render:
        fig = plt.figure()
        ax = fig.gca()
        fig.tight_layout()
        patch = ax.imshow(frames[0])
        ax.axis('off')
        def animate(i):
            patch.set_data(frames[i])
        anim = animation.FuncAnimation(plt.gcf(), animate, frames = len(frames), interval=20)
        return total_reward, np.array(all_observations, dtype=np.float64,), np.array(all_actions, dtype=np.float64), anim
    else:
        return total_reward, np.array(all_observations, dtype=np.float64,), np.array(all_actions, dtype=np.float64)

Let's first apply a random policy and see how the environment reacts. The random policy uniformly samples in the space of action.

In [38]:
def random_policy(state):
    return env.action_space.sample()

The animation is generated with the following commands:
```python
anim = run_one_episode(env, random_policy, max_steps=500, render=True, verbose=False)[-1]

with open('animation_random_policy.html', 'w') as f:
    f.write(anim.to_jshtml())
```

In [48]:
from IPython.display import HTML

HTML(filename="pilco/animation_random_policy.html")

## Fit the Dynamics Model

The dynamics model of pendulum can be written as
$$p(y_{t+1}|y_t, a_t)$$
where $y_t$ is the state vector at the time $t$ and $a_t$ is the action taken at the time $t$. PILCO uses a Gaussian process to model the above dynamics.

Given a sequence of state and action, we break them into the pairs of input and output for the above GP model. The below helper function is written to do so.

In [59]:
def prepare_data(state_list, action_list, win_in):
    """
    Prepares a list of states and a list of actions as inputs to the Gaussian Process for training.
    """
    
    X_list = []
    Y_list = []
    
    for state_array, action_array in zip(state_list, action_list):
        # the state and action array shape should be aligned.
        assert state_array.shape[0]-1 == action_array.shape[0]
        
        for i in range(state_array.shape[0]-win_in):
            Y_list.append(state_array[i+win_in:i+win_in+1])
            X_list.append(np.hstack([state_array[i:i+win_in].flatten(), action_array[i:i+win_in].flatten()]))
    X = np.vstack(X_list)
    Y = np.vstack(Y_list)
    return X, Y

In this example, we do a maximum likelihood estimate for the model hyper-parameters. In MXFusion, Gaussian process regression model is available as a module, which includes a dediated inference algorithm.

In [63]:
import mxnet as mx
from mxfusion import Model, Variable
from mxfusion.components.variables import PositiveTransformation
from mxfusion.components.distributions.gp.kernels import RBF
from mxfusion.modules.gp_modules import GPRegression
from mxfusion.inference import GradBasedInference, MAP

def fit_model(state_list, action_list, win_in, verbose=True):
    """
    Fits a Gaussian Process model to the state / action pairs passed in. 
    This creates a model of the environment which is used during
    policy optimization instead of querying the environment directly.
    
    See mxfusion.gp_modules for additional types of GP models to fit,
    including Sparse GP and Stochastic Varitional Inference Sparse GP.
    """
    X, Y = prepare_data(state_list, action_list, win_in)

    m = Model()
    m.N = Variable()
    m.X = Variable(shape=(m.N, X.shape[-1]))
    m.noise_var = Variable(shape=(1,), transformation=PositiveTransformation(),
                           initial_value=0.01)
    m.kernel = RBF(input_dim=X.shape[-1], variance=1, lengthscale=1, ARD=True)
    m.Y = GPRegression.define_variable(
        X=m.X, kernel=m.kernel, noise_var=m.noise_var,
        shape=(m.N, Y.shape[-1]))
    m.Y.factor.gp_log_pdf.jitter = 1e-6

    infr = GradBasedInference(
        inference_algorithm=MAP(model=m, observed=[m.X, m.Y]))
    infr.run(X=mx.nd.array(X, dtype='float64'),
             Y=mx.nd.array(Y, dtype='float64'),
             max_iter=1000, learning_rate=0.1, verbose=verbose)
    return m, infr, X, Y

### Policy Optimization

PILCO computes the expected reward of a policy given the dynamics model. First, we need to define the parametric form of the policy. In this example, we use a neural network with one hidden layer. As the action space is [-2, 2], we apply a tanh transformation and multiply the come with two. This enforces the returned actions stay within the range.

In [70]:
from mxnet.gluon import HybridBlock
from mxnet.gluon.nn import Dense

class NNController(HybridBlock):
    def __init__(self, prefix=None, params=None):
        super(NNController, self).__init__(prefix=prefix, params=params)
        self.dense1 = Dense(100, in_units=len(env.observation_space.high), dtype='float64', activation='relu')
        self.dense2 = Dense(1, in_units=100, dtype='float64', activation='tanh')
    def hybrid_forward(self, F, x):
        out = self.dense2(self.dense1(x))*2
        return out 
    
policy = NNController()
policy.collect_params().initialize(mx.initializer.Xavier(magnitude=1))

To compute the expected reward, we also need to define a reward function. This reward function is defined by us according to the task. The main component is the height of the pendulum. We also penalize the force and the angular momentum. 

In [39]:
class CostFunction(mx.gluon.HybridBlock):
    """
    The goal is to get the pendulum upright and stable as quickly as possible.
    Taken from the code for Pendulum.
    """
    def hybrid_forward(self, F, state, action):
        """
        :param state: [np.cos(theta), np.sin(theta), ~ momentum(theta)]
        a -> 0 when pendulum is upright, largest when pendulum is hanging down completely.
        b -> penalty for taking action
        c -> penalty for pendulum momentum
        """
        a_scale = 2.
        b_scale = .001
        c_scale = .1
        a = F.sum(a_scale * (state[:,:,0:1] -1) ** 2, axis=-1)
        b = F.sum(b_scale * action ** 2, axis=-1)
        c = F.sum(c_scale * state[:,:,2:3] ** 2, axis=-1)
        return (a + c + b)
    
cost = CostFunction()

The expected reward function can be written as
$$R = \mathbb{E}_{p(y_T, \ldots, y_0)}\left(\sum_{t=0}^T r(y_t)\right)$$
where $r(\cdot)$ is the reward function. $p(y_T, \ldots, y_0)$ is the joint distribution when applying the policy to the dynamics model:
$$p(y_T, \ldots, y_0) = p(y_0) \prod_{t=1}^T p(y_t|y_{t-1}, a_{t-1}),$$
where $a_{t-1} = \pi(y_{t-1})$ is the action taken at the time $t-1$, which is the outcome of the policy $\pi(\cdot)$.

The expected reward function is implemented as follows.

In [68]:
from mxfusion.inference.inference_alg import SamplingAlgorithm

class PolicyUpdateGPParametricApprox(SamplingAlgorithm):

    def compute(self, F, variables):
        
        s_0 = self.initial_state_generator(self.num_samples)
        a_0 = self.policy(s_0)
        a_t_plus_1 = a_0
        x_t = F.expand_dims(F.concat(s_0, a_0, dim=1), axis=1)

        gp = self.model.Y.factor
        sample_func = gp.draw_parametric_samples(F, variables, self.num_samples, self.approx_samples)
        cost = 0
        for t in range(self.n_time_steps):
            s_t_plus_1 = sample_func(F, x_t)
            cost = cost + self.cost_function(s_t_plus_1, a_t_plus_1)
            a_t_plus_1 = mx.nd.expand_dims(self.policy(s_t_plus_1), axis=2)
            x_t = mx.nd.concat(s_t_plus_1, a_t_plus_1, dim=2)
        total_cost = F.mean(cost)
        return total_cost, total_cost

We optimize the policy with respect to the expected reward by using a gradient optimizer.

In [40]:
from mxfusion.inference import GradTransferInference
from mxfusion.inference.pilco_alg import PolicyUpdateGPParametricApprox

def optimize_policy(policy, cost_func, model, infr, model_data_X, model_data_Y,
                    initial_state_generator, num_grad_steps,
                    learning_rate=1e-2, num_time_steps=100, 
                    num_samples=10, verbose=True):
    """
    Takes as primary inputs a policy, cost function, and trained model.
    Optimizes the policy for num_grad_steps number of iterations.
    """
    mb_alg = PolicyUpdateGPParametricApprox(
        model=model, observed=[model.X, model.Y], cost_function=cost_func,
        policy=policy, n_time_steps=num_time_steps,
        initial_state_generator=initial_state_generator,
        num_samples=num_samples)

    infr_pred = GradTransferInference(
        mb_alg, infr_params=infr.params, train_params=policy.collect_params())
    infr_pred.run(
        max_iter=num_grad_steps,
        X=mx.nd.array(model_data_X, dtype='float64'),
        Y=mx.nd.array(model_data_Y, dtype='float64'),
        verbose=verbose, learning_rate=learning_rate)
    return policy

## The Loop

We need to define a function that provides random initial states.

In [41]:
def initial_state_generator(num_initial_states):
    """
    Starts from valid states by drawing theta and momentum
    then computing np.cos(theta) and np.sin(theta) for state[0:2].s
    """
    return mx.nd.array(
        [env.observation_space.sample() for i in range(num_initial_states)],
        dtype='float64')

The loop of PILCO iterates the above three steps.

In [ ]:
num_episode = 20 # how many model fit + policy optimization episodes to run
num_samples = 100 # how many sample trajectories the policy optimization loop uses
num_grad_steps = 1000 # how many gradient steps the optimizer takes per episode
num_time_steps = 100 # how far to roll out each sample trajectory
learning_rate = 1e-3 # learning rate for the policy optimization

all_states = []
all_actions = []

for i_ep in range(num_episode):
    # Run an episode and collect data.
    if i_ep == 0:
        policy_func = lambda x: env.action_space.sample()
    else:
        policy_func = lambda x: policy(mx.nd.expand_dims(mx.nd.array(x, dtype='float64'), axis=0)).asnumpy()[0]
    total_reward, states, actions = run_one_episode(
        env, policy_func, max_steps=num_time_steps)
    all_states.append(states)
    all_actions.append(actions)

    # Fit a model.
    model, infr, model_data_X, model_data_Y = fit_model(
        all_states, all_actions, win_in=1, verbose=True)

    # Optimize the policy.
    policy = optimize_policy(
        policy, cost, model, infr, model_data_X, model_data_Y,
        initial_state_generator, num_grad_steps=num_grad_steps,
        num_samples=num_samples, learning_rate=learning_rate,
        num_time_steps=num_time_steps)

Policy after the first episode (random exploration):

In [69]:
HTML(filename="pilco/animation_policy_iter_0.html")

Policy after the 5th episode:

In [56]:
HTML(filename="pilco/animation_policy_iter_4.html")

## Reference

M. P. Deisenroth, C. E. Rasmussen. 2011. "PILCO: A Model-Based and Data-Efficient Approach to Policy Search". _in
Proceedings of the 28th International Conference on Machine Learning._ [http://mlg.eng.cam.ac.uk/pub/pdf/DeiRas11.pdf](http://mlg.eng.cam.ac.uk/pub/pdf/DeiRas11.pdf)
